In [36]:
import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings('ignore')
data=pd.read_csv('data.csv',index_col=0)
data=data.replace(',','',regex=True)
data=data.astype(float)




###월말 데이터
month_end=[]
for i in range(len(data)-1):

    if data.index[i][5:7]!=data.index[i+1][5:7]:
        month_end.append(data.index[i])
########
#rtn=np.log(data/data.shift(1))

data=data.drop('A114800',axis=1)







## 모멘텀 지표 구현

In [34]:
#data=data.drop(['A139660','A114800'],axis=1)

In [3]:
def rolling_operation(data,rolling):
    data_moving_average=data.rolling(rolling).mean()
    data_abs_rtn=np.abs(np.log(data/data.shift(1)))
    data_rolling_risk_adjusted=np.log(data/data.shift(rolling))/(data_abs_rtn.rolling(rolling).sum())
    
    ###각 종목과 나머지 포트폴리오의  rolling correaltion
    data_rtn=np.log(data/data.shift(1))
    universe=set(data_rtn.columns)
    port=np.sum(data_rtn[list(universe.difference(set(list(universe)[0])))],axis=1)
    stock=data_rtn[list(universe)[0]]
    corr=pd.concat([port,stock],axis=1).rolling(rolling).corr().reset_index()
    corr.columns=['date','code','corr','non']
    corr=corr.loc[corr['code']==list(universe)[0]]

    for code in list(universe)[1:]:
        port=np.sum(data_rtn[list(universe.difference(set(code)))],axis=1)
        stock=data_rtn[code]
        tmp=pd.concat([port,stock],axis=1).rolling(rolling).corr().reset_index()
        tmp.columns=['date','code','corr','non']
        tmp=tmp.loc[tmp['code']==code]
        corr=corr.append(tmp)
    corr=corr[['date','code','corr']]

    
    
    data=data.stack().reset_index()
    data.columns=['date','code','close']
    data_moving_average=data_moving_average.stack().reset_index()
    data_moving_average.columns=['date','code','sma']
    data_rolling_risk_adjusted=data_rolling_risk_adjusted.stack().reset_index()
    data_rolling_risk_adjusted.columns=['date','code','rolling_risk_adjusted']
    data=data.set_index(['date','code']).join(data_moving_average.set_index(['date','code']))
    data=data.join(data_rolling_risk_adjusted.set_index(['date','code']))
    data=data.join(corr.set_index(['date','code'])).reset_index()
    
    data['price_minus_moving_average']=(data['close']/data['sma'])-1
    data['total_return_momentum']=np.log(data.groupby('code')['close'].shift(0)/data.groupby('code')['close'].shift(rolling))
    data['correlation_adjustment1']=data['rolling_risk_adjusted']*(1-data['corr'])
    data['correlation_adjustment2']=data['rolling_risk_adjusted']/(1+data['corr'])
    return data


#### 실험삼아 출력

In [4]:
#test_data=rolling_operation(data=data,rolling=30)
test_data=rolling_operation(data=data,rolling=250)

## backtest 

구차나서 옵티멀 하게는 안짬

In [5]:
def backtest(p, width,factor,month_end=month_end,temp_data=test_data):
    temp_data['rtn']=np.log(temp_data.groupby('code').close.shift(0)/temp_data.groupby('code').close.shift(1))
    daily_rtn=pd.pivot_table(temp_data[['date','code','rtn']],index='date',values='rtn',columns=['code'],aggfunc='first',dropna=False)
    factor_df1=pd.pivot_table(temp_data[['date','code',factor]],index='date',values=factor,columns=['code'],aggfunc='first',dropna=False)
    factor_df1=factor_df1.fillna(method='ffill')
    return_tickers=dict()
    daily_index=list(daily_rtn.index)
    factor_df1=factor_df1.shift(1)### 선견편향 제거
    factor_df1=factor_df1.loc[month_end]

    for i in range(0,len(factor_df1)-1):   
        
        first_sort=factor_df1.iloc[i].dropna().rank(ascending=False,method='first')\
            [(factor_df1.iloc[i].dropna().rank(ascending=False,method='first')>(len(factor_df1.iloc[i].dropna())*(p-width)))&\
            (factor_df1.iloc[i].dropna().rank(ascending=False,method='first')<(len(factor_df1.iloc[i].dropna())*p))].index.values
        first_sort=list(first_sort)
        start=daily_index.index(factor_df1.index[i])
        if i!=0:
            temp_daily=daily_rtn.loc[daily_index[start+1]:factor_df1.index[i+1]]
        else:
            temp_daily=daily_rtn.loc[:factor_df1.index[i]]
        for day in temp_daily.index:
        
            return_tickers[day] = \
            [[np.nanmean(daily_rtn.loc[day].reindex(first_sort).dropna().values )], first_sort]

    
    return return_tickers

In [30]:
import plotly.express as px
import warnings
from tqdm import tqdm
warnings.filterwarnings('ignore')
portfolio_result=pd.DataFrame()
ps=[0.33,0.66,0.99]
rollings=[30,60,180,250,500]
factors=['correlation_adjustment1','correlation_adjustment2','price_minus_moving_average', 'total_return_momentum']
for rolling in tqdm(rollings):
    test_data=rolling_operation(data=data,rolling=rolling)
    for factor in factors:
        for p in ps:
            result=backtest(factor=factor,p=p,width=0.33)
            portfolio_result[f"factor:{factor}_rolling_{rolling}_{round(p*3)}"]=pd.Series(np.array([rtn[0] for rtn in list(result.values())]).flatten(), index = result.keys())
fig=px.line((1+portfolio_result.dropna(how='all')).cumprod())
fig.show()


100%|██████████| 5/5 [01:46<00:00, 21.39s/it]


### sharpe ratio

In [40]:
for col in portfolio_result:
    print(col)
    tmp_port=portfolio_result[col]
    print((np.prod(tmp_port + 1) ** (252 / tmp_port.dropna().shape[0]) - 1)/(np.std(tmp_port)*np.sqrt(252)))
    print()

factor:correlation_adjustment1_rolling_30_1
0.41645156430232294

factor:correlation_adjustment1_rolling_30_2
0.4595644818100249

factor:correlation_adjustment1_rolling_30_3
0.04029706452778266

factor:correlation_adjustment2_rolling_30_1
0.48663596726478475

factor:correlation_adjustment2_rolling_30_2
0.37783461180282285

factor:correlation_adjustment2_rolling_30_3
0.0866282357933068

factor:price_minus_moving_average_rolling_30_1
0.13284578869697206

factor:price_minus_moving_average_rolling_30_2
0.3132222530120063

factor:price_minus_moving_average_rolling_30_3
0.46409060772464406

factor:total_return_momentum_rolling_30_1
0.26964031389738113

factor:total_return_momentum_rolling_30_2
0.3414405311096246

factor:total_return_momentum_rolling_30_3
0.34577768695571764

factor:correlation_adjustment1_rolling_60_1
0.41645156430232294

factor:correlation_adjustment1_rolling_60_2
0.4595644818100249

factor:correlation_adjustment1_rolling_60_3
0.04029706452778266

factor:correlation_adjustme

#### MDD

In [32]:
def get_mdd(x):
    """
    MDD(Maximum Draw-Down)
    :return: (peak_upper, peak_lower, mdd rate)
    """
    arr_v = np.array(x.fillna(method='ffill'))
    peak_lower = np.argmax(np.maximum.accumulate(arr_v) - arr_v)
    peak_upper = np.argmax(arr_v[:peak_lower])
    return  (arr_v[peak_lower] - arr_v[peak_upper]) / arr_v[peak_upper]



for col in portfolio_result.columns:
    arr=(1+portfolio_result.dropna(how='all')[col]).cumprod()
    print(col)
    print(get_mdd(arr))
    print()

factor:correlation_adjustment1_rolling_30_1
-0.16536426602403967

factor:correlation_adjustment1_rolling_30_2
-0.24221253419401223

factor:correlation_adjustment1_rolling_30_3
-0.3693888119662231

factor:correlation_adjustment2_rolling_30_1
-0.1549600958050626

factor:correlation_adjustment2_rolling_30_2
-0.2460575986319261

factor:correlation_adjustment2_rolling_30_3
-0.36328835876167354

factor:price_minus_moving_average_rolling_30_1
-0.3501559635056502

factor:price_minus_moving_average_rolling_30_2
-0.24874707626616455

factor:price_minus_moving_average_rolling_30_3
-0.3457426021374943

factor:total_return_momentum_rolling_30_1
-0.288067203778321

factor:total_return_momentum_rolling_30_2
-0.24872495186047008

factor:total_return_momentum_rolling_30_3
-0.2957314228459495

factor:correlation_adjustment1_rolling_60_1
-0.16536426602403967

factor:correlation_adjustment1_rolling_60_2
-0.24221253419401223

factor:correlation_adjustment1_rolling_60_3
-0.3693888119662231

factor:correlati

In [37]:
trading_data=rolling_operation(data=data,rolling=250)
def print_show_trading(p, width,factor,month_end=month_end,temp_data=trading_data):
    temp_data['rtn']=np.log(temp_data.groupby('code').close.shift(0)/temp_data.groupby('code').close.shift(1))
    daily_rtn=pd.pivot_table(temp_data[['date','code','rtn']],index='date',values='rtn',columns=['code'],aggfunc='first',dropna=False)
    factor_df1=pd.pivot_table(temp_data[['date','code',factor]],index='date',values=factor,columns=['code'],aggfunc='first',dropna=False)
    factor_df1=factor_df1.fillna(method='ffill')
    
    first_sort=factor_df1.iloc[-1].dropna().rank(ascending=False,method='first')\
            [(factor_df1.iloc[-1].dropna().rank(ascending=False,method='first')>(len(factor_df1.iloc[-1].dropna())*(p-width)))&\
            (factor_df1.iloc[-1].dropna().rank(ascending=False,method='first')<(len(factor_df1.iloc[-1].dropna())*p))].index.values
    first_sort=list(first_sort)
  
    return first_sort
   
  
  
  


85/4